# Validation Examples
#### Frederik Kelbel, Imperial College London

## Dependencies

In [1]:
import torch
import plotly.graph_objects as go
import numpy as np
from operators import div, Δ


from DGM import DGMSolver
from pdes import PDE
from scipy.integrate import quad
from plotly.subplots import make_subplots
from configs import CONFIG_PARABOLIC_PDES as MODEL_CONFIG

## Plotting

In [2]:
def plot_losses(losses, avg_over=10):
    avgs = np.convolve(losses, np.ones(avg_over), 'valid') / avg_over
    fig = make_subplots(rows=1, cols=1)
    fig.add_trace(go.Scatter(x=np.arange(len(avgs)), y=avgs, mode='lines', name="Error at x=0.1"), row=1, col=1)
    fig.update_layout(
        title="Loss",
        xaxis_title="Iterations",
        yaxis_title="Loss",
        font=dict(
            family="Courier New, monospace",
            size=14
        )
    )
    fig.show()
    
def plot_1D_functions(solver, sol):
    fig = make_subplots(rows=1, cols=2, 
                   specs=[[{'type': 'surface'}, {'type': 'surface'}]])
    xs = np.linspace(0, 1, 100)
    ts = np.linspace(0.01, 1, 100)
    us_pred = np.array([[solver.u(x, t) for x in xs] for t in ts])
    us = np.array([[sol(x, t) for x in xs] for t in ts])
    x_mesh, t_mesh = np.meshgrid(xs, ts)
    fig.add_trace(go.Surface(z=us, showscale=False), row=1, col=1)
    fig.add_trace(go.Surface(z=us_pred), row=1, col=2)
    fig.update_layout(title='Solution | Approximation',
                  scene = dict(
                    xaxis_title="t",
                    yaxis_title="x",
                    zaxis_title="u(x, t)"),
                  scene2 = dict(
                    xaxis_title="t",
                    yaxis_title="x",
                    zaxis_title="u(x, t)"),
                  margin=dict(l=50, r=50, b=50, t=50))
    fig.show()

## Partial Differential Equations

### Nonhomogeneous Transport:
$$
\begin{cases}
u_t + b (\nabla \cdot u) = f \quad & \text{in } [0, 1]^\texttt{x_dim=1} \times [0, 1]\\
u = g \quad & \text{on } [0, 1]^\texttt{x_dim=1} \times {t=0}
\end{cases}
$$

In [3]:
class TRANSPORT(PDE):
    def __init__(self):
        super().__init__()
        self.b = 0.3
        self.f = lambda x, t: 2*t + x*t
        self.g = lambda x: x
        self.var_dim = 2 # var = (x, t)
        self.equation = lambda u, var: div(u, var[1]) + self.b * div(u, var[0]) - self.f(var[0], var[1])
        self.domain_func = [(lambda var: var, 64)]
        self.boundary_cond = [lambda u, var: u -self.g(var[0])]
        self.boundary_func = [(lambda var: [var[0], var[1]*0], 64)]
        

In [4]:
eq = TRANSPORT()
model = MODEL_CONFIG
solver = DGMSolver(model, eq)
losses = list(solver.train(200))
plot_losses(losses)

100%|██████████| 200/200 [00:02<00:00, 72.87 it/s]


In [5]:
if eq.var_dim == 2:
    f = lambda s, x, t, b: eq.f(x+(s-t)*b, s)
    Transport_sol =\
        lambda x, t: eq.g(x-eq.b*t) + quad(f, 0, t, args=(x, t, eq.b))[0]
    plot_1D_functions(solver, Transport_sol)

### Inviscid Burger's Equation:
$$
\begin{cases}
u_t + u (\nabla \cdot u) = 0 \quad & \text{in } [0, 1]^\texttt{x_dim=1} \times [0, 1]\\
u = g \quad & \text{on } [0, 1]^\texttt{x_dim=1} \times {t=0}
\end{cases}
$$

In [6]:
class INVISCID_BURGERS(PDE):
    def __init__(self):
        super().__init__()
        self.var_dim = 2 # var = (x, t)
        self.equation = lambda u, var: div(u, var[1]) + u * div(u, var[0])
        self.domain_func = [(lambda var: var, 64)]
        self.boundary_cond = [lambda u, var: u - var[0]]
        self.boundary_func = [(lambda var: [var[0], var[1]*0], 64)]

In [7]:
eq = INVISCID_BURGERS()
model = MODEL_CONFIG
solver = DGMSolver(model, eq)
losses = list(solver.train(300))
plot_losses(losses)

100%|██████████| 300/300 [00:04<00:00, 71.89 it/s]


In [8]:
if eq.var_dim==2:
    INVISCID_BURGERS_sol = lambda x, t: x / (1 + t)
    plot_1D_functions(solver, INVISCID_BURGERS_sol)

### Diffusion Advection Equation:
$$
\begin{cases}
u_t + a u_x - b \Delta u = 0 \quad & \text{in } [0, 1]^{\texttt{x_dim}=1} \times [0, 1]\\
u = \exp\Big( -\frac{(x-1)^2}{b}\Big) \quad & \text{on } [0, 1]^{\texttt{x_dim}=1} \times {t=0} \\
u = \frac{1}{\sqrt{4t+1}} \exp\Big(-\frac{(x-1-at)^2}{b(4t+1)} \Big) \quad & \text{on } \{0, 1\}^{\texttt{x_dim}=1}\times [0, 1]
\end{cases}
$$

In [9]:
class HEAT(PDE):
    def __init__(self):
        super().__init__()
        self.a = 0.01
        self.b = 10
        self.var_dim = 2
        self.equation = lambda u, var: div(u, var[1]) + self.a * div(u, var[0]) - self.b * Δ(u, var[0])
        self.domain_func = [(lambda var: var, 64)]
        self.boundary_cond = [lambda u, var: u - 1/torch.sqrt(4*var[1]+1)*torch.exp(-(var[0]-1-self.a*var[0])**2/(self.b*(4*var[1]+1))),
                             lambda u, var: u - torch.exp(-(var[0]-1)**2/self.b)]
        self.boundary_func = [(lambda var: [torch.where(var[0] > 0.5, 1.0, 0.0), var[1]], 16),
                             (lambda var: [var[0], var[1]*0], 16)]

In [10]:
HEAT_MODEL_CONFIG = {
    "batch_size":128, # minimum batch size is two because of split
    "hidden_dim": 128,
    "learning_rate": 5e-3,
    "loss_weights": (1, 3),
    "sampling_method": "uniform",
    "lr_decay": 0.98,
    "network_type": "GRU",
    "optimiser": "Adam"
}
eq = HEAT()
model = HEAT_MODEL_CONFIG
solver = DGMSolver(model, eq)
losses = list(solver.train(600))
plot_losses(losses)

100%|██████████| 600/600 [00:23<00:00, 25.95 it/s]


In [11]:
if eq.var_dim == 2:
    HEAT_sol = lambda x, t: 1/np.sqrt(4*t+1)*np.exp(-(x-1-eq.a*t)**2/(eq.b*(4*t+1)))
    plot_1D_functions(solver, HEAT_sol)

### Transport Equation in 2D:
$$
\begin{cases}
u_t + y u_x - x u_y = 0 \quad & \text{in } [0, 1]^\texttt{2} \times [0, 1]\\
u = \exp(-(x-1)^2 -(y-1)^2) \quad & \text{on } [0, 1]^\texttt{2} \times {t=0}
\end{cases}
$$

In [12]:
class TRANSPORT2D(PDE):
    def __init__(self):
        super().__init__()
        self.var_dim = 3 # var = (x, y, t)
        self.equation = lambda u, var: div(u, var[2]) + var[1]*div(u, var[0]) - var[0]*div(u, var[1]) 
        self.domain_func = [(lambda var: var, 128)]
        self.boundary_cond = [lambda u, var: u -torch.exp(-(var[0]-1)**2-(var[1]-1)**2)]
        self.boundary_func = [(lambda var: var[0:2] + [var[1]*0], 32)]
      

In [13]:
TRANSPORT2D_MODEL_CONFIG = {
    "batch_size":256, # minimum batch size is two because of split
    "hidden_dim": 64,
    "learning_rate": 5e-3,
    "loss_weights": (2, 1),
    "sampling_method": "uniform",
    "lr_decay": 0.98,
    "network_type": "DGM",
    "optimiser": "Adam"
}
eq = TRANSPORT2D()
model = TRANSPORT2D_MODEL_CONFIG
solver = DGMSolver(model, eq)
losses = list(solver.train(900))
plot_losses(losses)

100%|██████████| 900/900 [00:18<00:00, 49.90 it/s]


In [14]:
TRANSPORT2D_sol = lambda x, y, t: np.exp(-(x**2+y**2)+2*(x+y)*np.cos(t)+2*(x-y)*np.sin(t)-2)
domain_error = np.sum([[[np.abs(solver.u(x, y, t)-TRANSPORT2D_sol(x, y, t)) for x in np.linspace(0, 1, 50)] for y in np.linspace(0, 1, 50)] for t in np.linspace(0.01, 1,10)], axis=0)
print("Mean domain error: ", domain_error.mean())

Mean domain error:  0.12755398013752978


In [15]:
domain_error = np.sum([[[np.abs(solver.u(x, y, t)-TRANSPORT2D_sol(x, y, t)) for x in np.linspace(0, 1, 50)] for y in np.linspace(0, 1, 50)] for t in np.linspace(0.01, 1,10)], axis=0)

In [18]:
fig = make_subplots(rows=1, cols=1, specs=[[{'type': 'heatmap'}]])
fig.add_trace(go.Heatmap(z=domain_error, coloraxis = "coloraxis", zsmooth='best'), row=1, col=1)
fig.update_layout(title='Error density',
                  coloraxis = {'colorscale':'Viridis'},
                  xaxis_title="x",
                  yaxis_title="y",
                  margin=dict(l=20, r=20, b=20, t=50))
fig.show()

### Fokker-Planck Equation for the OU Process:
$$
\begin{cases}
\partial_t p + k p + k(x-\mu) \partial_x p - \frac{1}{2} \sigma^2 \partial_{xx} p = 0\\
p(0, x) = \delta(x - x_0) \approx \lim_{a \rightarrow 0}\frac{1}{|a| \sqrt{\pi}} e^{-(\frac{x-x_0}{a})^2} \quad & \text{on } [0, 1]^{\texttt{x_dim}=1} \times {t=0} \\
\end{cases}
$$

Notes: Exponentiating assumes to much knowledge. PIADGM paper is cheating. GRUNetwork performs better for some reason.

In [19]:
class OUPROCESS(PDE):
    def __init__(self):
        super().__init__()
        self.mu = 0.5
        self.sigma = 2.0
        self.k = 0.0
        a = 0.25
        self.var_dim = 2 # var = (x, t)   
        self.equation = lambda p, var: div(p, var[1]) + self.k*p + self.k*(var[0]-self.mu)*div(p, var[0])-(1/2)*self.sigma**2*Δ(p, var[0])
        self.domain_func = [(lambda var: [8*var[0]-4, var[1]], 64)]
        self.boundary_cond = [lambda p, var: p -(1/np.sqrt(2*np.pi*a))*torch.exp(-(var[0]**2/(2*a))),
                             lambda p, var: 5*torch.clamp(p, max=0)]
        self.boundary_func = [(lambda var: [8*var[0]-4, 0*var[1]], 64),
                             (lambda var: var, 64)]

In [20]:
CONFIG_OU = {
    "hidden_dim": 64,
    "learning_rate": 5e-3,
    "loss_weights": (1.5, 1),
    "lr_decay": 0.99,
    "sampling_method": "uniform",
    "network_type": "GRU",
    "optimiser": "Adam"
}
eq = OUPROCESS()
model = CONFIG_OU
solver = DGMSolver(model, eq)
losses = list(solver.train(1100))
plot_losses(losses)

100%|██████████| 1100/1100 [00:17<00:00, 61.67 it/s]


In [21]:
fig = make_subplots(rows=1, cols=1, specs=[[{'type': 'surface'}]])
xs = np.linspace(-4, 4, 100)
ts = np.linspace(0.01, 1, 100)
us_pred = np.array([[solver.u(x, t) for x in xs] for t in ts])
norms = [np.trapz(us, xs) for us in us_pred]
us_pred = np.array([ us/n for us, n in zip(us_pred, norms)])
fig.add_trace(go.Surface(x=xs, y=ts, z=us_pred), row=1, col=1)
fig.update_layout(title='Solution | Approximation',
                  scene = dict(
                      xaxis_title="x",
                      yaxis_title="t",
                      zaxis_title="p(x, t)"),
                  margin=dict(l=50, r=50, b=50, t=50))
fig.show()